In [1]:
import pandas as pd
import json

In [2]:
df = pd.read_csv('../data/logs/day1.csv')
df.head()

id    sid   time
0  11396  11502  25240
1  11396  11402  25249
2  11396  11403  25256
3  11396  11404  25263
4  11396  11405  25270

In [4]:
def Id_move_record(df):
    #获得每个人的移动记录
    group = df.groupby('id')
    people = []
    for key, group in group:
        p = {'id': int(key), 'l':[]}
        timelist = group['time'].to_list()
        sidlist = group['sid'].to_list()
        for i in range(len(timelist)):
            p['l'].append([timelist[i], sidlist[i]])
        people.append(p)
    return people
data = Id_move_record(df)
# data

In [5]:
#根据上面数据获得每个人在每个传感器进入的次数（每次进入的时间）和停留的时间（起始时间和停留时间）
from collections import defaultdict
def move_and_stay(data):
    result = []
    for p in data:
        pid = p['id']
        sensors = []
        indexBySid = defaultdict(lambda: None)
        for i in range(len(p['l'])):
            l = p['l'][i]
            sid = l[1]
            time = l[0]
            index = indexBySid[sid]
            
#             #记录进入时刻
#             if index:
#                 s = sensors[index]
#                 s[2].append(time)
#             else:
#                 #添加传感器
#                 indexBySid[sid] = len(sensors)
#                 sensors.append([
#                     sid,
#                     [],
#                     [time]
#                 ])
            
            #计算停留时间
            if i > 0:
                #计算停留时间
                psid = p['l'][i - 1][1]
                ptime = p['l'][i - 1][0]
                pindex = indexBySid[sid]
                if pindex:
                    ps = sensors[pindex]
                    ps[1] += (time - ptime)
                else:
                    #添加传感器
                    indexBySid[psid] = len(sensors)
#                     sensors.append([
#                         psid,
#                         [[ptime, time - ptime]]
#                     ])
                    sensors.append([
                        psid,
                        time - ptime #停留时刻
                    ])
        #添加结果
        result.append({
            'id': pid,
            'sensors': sensors
        })
    return result
result = move_and_stay(data)
len(result), result

(3564,
 [{'id': 10001,
   'sensors': [[11502, [[50580, 8]]],
    [11402, [[50588, 8]]],
    [11303, [[50596, 243]]],
    [11403, [[50839, 7]]],
    [11404, [[50846, 7]]],
    [11305, [[50853, 12]]],
    [11206, [[50865, 10]]],
    [11106, [[50875, 8]]],
    [11006, [[50883, 9], [62558, 15]]],
    [10906, [[50892, 10], [59762, 10], [62541, 17]]],
    [10905, [[50902, 26], [59772, 9]]],
    [10805, [[50928, 6361]]],
    [10806, [[57289, 16]]],
    [10807, [[57305, 13]]],
    [10708, [[57318, 14]]],
    [10709, [[57332, 857], [59157, 8]]],
    [10609, [[58189, 15], [59147, 10]]],
    [10509, [[58204, 16], [59139, 8]]],
    [10409, [[58220, 12], [58232, 287]]],
    [10409, [[58519, 12], [58531, 608]]],
    [10709, [[59165, 16]]],
    [10808, [[59181, 8]]],
    [10908, [[59189, 8]]],
    [11009, [[59197, 12]]],
    [11109, [[59209, 10]]],
    [11209, [[59219, 8], [59720, 20]]],
    [11310, [[59227, 8], [59710, 10]]],
    [11411, [[59235, 8], [59659, 16]]],
    [11410, [[59243, 9], [59650, 9

In [12]:
def move_between_sid(df):
    #获得每个时间刻人在传感器之间的转移情况
    group = df.groupby('id')
    log = []
    for key, group in group:
        timelist = group['time'].to_list()
        sidlist = group['sid'].to_list()
        for i in range(len(timelist)):
            if(i > 0):
                log.append([timelist[i], sidlist[i], sidlist[i - 1]])
    return log
# log = move_between_sid(df)

[[50588, 11402, 11502],
 [50596, 11303, 11402],
 [50839, 11403, 11303],
 [50846, 11404, 11403],
 [50853, 11305, 11404],
 [50865, 11206, 11305],
 [50875, 11106, 11206],
 [50883, 11006, 11106],
 [50892, 10906, 11006],
 [50902, 10905, 10906],
 [50928, 10805, 10905],
 [57289, 10806, 10805],
 [57305, 10807, 10806],
 [57318, 10708, 10807],
 [57332, 10709, 10708],
 [58189, 10609, 10709],
 [58204, 10509, 10609],
 [58220, 10409, 10509],
 [58232, 10410, 10409],
 [58519, 10409, 10410],
 [58531, 10308, 10409],
 [59139, 10409, 10308],
 [59147, 10509, 10409],
 [59157, 10609, 10509],
 [59165, 10709, 10609],
 [59181, 10808, 10709],
 [59189, 10908, 10808],
 [59197, 11009, 10908],
 [59209, 11109, 11009],
 [59219, 11209, 11109],
 [59227, 11310, 11209],
 [59235, 11411, 11310],
 [59243, 11410, 11411],
 [59252, 21411, 11410],
 [59268, 21410, 21411],
 [59276, 21409, 21410],
 [59284, 21408, 21409],
 [59292, 21407, 21408],
 [59300, 21406, 21407],
 [59308, 21405, 21406],
 [59325, 21404, 21405],
 [59336, 21403, 

In [26]:
def merge_log_by_time(data):
    df = pd.DataFrame(data)
    grouped = df.groupby(0)
    result = []
    for key, group in grouped:
        d = {'time': int(key), 'm': []}
        s = set()
        indexBySet = {}
        fromlist = group[2].to_list()
        tolist = group[1].to_list()
        for i in range(len(fromlist)):
            f = fromlist[i]
            t = tolist[i]
            if (f, t) in s:
                index = indexBySet[(f, t)]
                d['m'][index][2] += 1
            else:
                indexBySet[(f, t)] = len(d['m'])
                d['m'].append([f, t, 1])
                s.add((f, t))
        result.append(d)
    return result
# log_by_time = merge_log_by_time(log)
# log_by_time

[{'time': 25249, 'm': [[11502, 11402, 1]]},
 {'time': 25256, 'm': [[11402, 11403, 1]]},
 {'time': 25263, 'm': [[11403, 11404, 1]]},
 {'time': 25270, 'm': [[11404, 11405, 1]]},
 {'time': 25277, 'm': [[11405, 11306, 1]]},
 {'time': 25284, 'm': [[11306, 11307, 1]]},
 {'time': 25291, 'm': [[11307, 11308, 1]]},
 {'time': 25298, 'm': [[11308, 11309, 1]]},
 {'time': 25305, 'm': [[11309, 11310, 1]]},
 {'time': 25312, 'm': [[11310, 11411, 1]]},
 {'time': 25319, 'm': [[11411, 11410, 1]]},
 {'time': 25328, 'm': [[11410, 21411, 1]]},
 {'time': 25329, 'm': [[11300, 11301, 1]]},
 {'time': 25336, 'm': [[11301, 11302, 1]]},
 {'time': 25343, 'm': [[11302, 11403, 1]]},
 {'time': 25344, 'm': [[21411, 21410, 1]]},
 {'time': 25350, 'm': [[11403, 11404, 1]]},
 {'time': 25351, 'm': [[21410, 21310, 1]]},
 {'time': 25357, 'm': [[11404, 11405, 1]]},
 {'time': 25358, 'm': [[21310, 21209, 1]]},
 {'time': 25364, 'm': [[11405, 11406, 1]]},
 {'time': 25365, 'm': [[21209, 21109, 1]]},
 {'time': 25371, 'm': [[11406, 1

In [6]:
import json
def save_to_json(data):
    with open('../data/people/sid_log_day1.json', 'w') as f:
        json.dump(data, f, ensure_ascii=False)

In [7]:
save_to_json(result)